De acuerdo con lo sugerido por: `https://towardsdatascience.com/particle-tracking-at-cern-with-machine-learning-4cb6b255613c`, se puede optimizar el tratamiento de los datos asumiendo que se los puede agrupar con la forma de un cluster de hélice. 

La justificación es que existe un campo magnético que está presente, caso contrario las partículas describirían una trayectoria en línea recta. 

El momento de las partículas también afecta a la tensión de la espiral, cuanto mayor sea el momento, más recta será la trayectoria. 

In [1]:
import pandas as pd


In [2]:
cells_data = pd.read_csv("data/train/train_1/event000001000-cells.csv")
hits_data = pd.read_csv("data/train/train_1/event000001000-hits.csv")
particles_data = pd.read_csv("data/train/train_1/event000001000-particles.csv")
truth_data = pd.read_csv("data/train/train_1/event000001000-truth.csv")

# Datasets

## Event Hits dataset

Por cada entrada, se dispone de la siguiente información: 
* **hit_id**: identificador numérico del hit dentro del evento
* **x, y, z**: medidas de la posición en x, y, z en milímetros, del golpe, con respecto a coordenadas globales. 
* **volume_id**: identificador numérico del grupo detector. 
* **layer_id**: identificador numérico de la capa dentro del grupo. 
* **module_id**: identificador numérico del módulo dentro de la capa

El volumen/capa/módulo podría ser deducido de x, y, z. Se proveen para simplificar el manejo de datos específico del detector.  

In [3]:
hits_data.head(4)

hit_id        x         y       z  volume_id  layer_id  module_id
0       1 -64.4099 -7.163700 -1502.5          7         2          1
1       2 -55.3361  0.635342 -1502.5          7         2          1
2       3 -83.8305 -1.143010 -1502.5          7         2          1
3       4 -96.1091 -8.241030 -1502.5          7         2          1

## Event truth dataset 

Contiene el mapeo entre los hits y la generación de partículas, y el verdadero estado de la partícula en cada medición del hit. Cada entrada mapea un hit a una partícula. 
* **hit_id**: identificador numérico del hit definido en el dataset de hits. 
* **particle_id**: identificador numérico de la partícula de acuerdo a lo definido en el archivo de partículas. Un valor de 0 significa que el hit no originó una partícula reconstruible pero, por ejemplo, se detectó ruido. 
* **tx, ty, tz**: la verdadera intersección en las coordinadas globales (en milímetros) entre la trayectoria de la particula y la superficie sensible. 
* **tpx, tpy, tpz**: el momento verdadero (en GeV/c, gigaelectrovoltio / velocidad de la luz) en el punto de intersección en las coordenadas globales. 
* **weight**: peso por golpe utilizado para la métrica de puntuación; suma total de los pesos de cada evento es igual a uno. 

In [4]:
truth_data.head(4)

hit_id         particle_id       tx        ty      tz            tpx  \
0       1                   0 -64.4116 -7.164120 -1502.5  250710.000000   
1       2   22525763437723648 -55.3385  0.630805 -1502.5      -0.570605   
2       3                   0 -83.8280 -1.145580 -1502.5  626295.000000   
3       4  297237712845406208 -96.1229 -8.230360 -1502.5      -0.225235   

             tpy           tpz    weight  
0 -149908.000000 -956385.00000  0.000000  
1       0.028390     -15.49220  0.000010  
2 -169767.000000 -760877.00000  0.000000  
3      -0.050968      -3.70232  0.000008

## Event particles dataset

Contiene los siguientes valores por cada partícula/entrada: 
* **particle_id**: identificador numérico de la partícula dentro del evento. 
* **vx, vy, vz**: posición inicial o vertex (en milímetros) en coordinadas globales
* **px, py, pz**: momento inicial (en GeV/c) a lo largo del eje global. 
* **q**: carga de la partícula (como múltiplo de la carga electrónica absoluta)
* **n_hits**: número de hits generados por esta partícula. 

Todas las entradas poseen la información generada o verdad fundamental. 

In [5]:
particles_data.head(4)

particle_id        vx        vy        vz        px        py  \
0  4503668346847232 -0.009288  0.009861 -0.077879 -0.055269  0.323272   
1  4503737066323968 -0.009288  0.009861 -0.077879 -0.948125  0.470892   
2  4503805785800704 -0.009288  0.009861 -0.077879 -0.886484  0.105749   
3  4503874505277440 -0.009288  0.009861 -0.077879  0.257539 -0.676718   

         pz  q  nhits  
0 -0.203492 -1      8  
1  2.010060  1     11  
2  0.683881 -1      0  
3  0.991616  1     12

## Event hit cells dataset

El archivo de células contiene las células detectoras constituyentes activas que comprenden cada golpe. Puede ser usado para refinar el hit a la asociación de la pista. Una célula es la granularidad más pequeña dentro de cada módulo detector, como un pixel en una pantalla, con la diferencia de que, de acuerdo con el `volume_id` la célula puede ser un cuadrado o un rectángulo. Se encuentra identificado por dos canales identificadores que son únicos dentro de cada módulo del detector y codifican una posición al igual que los números de columna/fila de una matriz.  
Una célula puede proveer información de señal que el módulo detector grabó en adición a la posición. Dependiendo del tipo detector sólo uno de los canales identificadores es válido, por ejemplo, los detectores de tiras y el valor podría tener una resolución diferente. 
* **hit_id**: identificador numérico del hit de acuerdo con su definición en el archivo de hits.
* **ch0, ch1**: identificador único del canal, coordenadas dentro de un módulo. 
* **value**: valor de la información de señal, por ejemplo, cuánta carga una partícula tiene depositada. 


In [6]:
cells_data.head(4)

hit_id  ch0  ch1     value
0       1  209  617  0.013832
1       1  210  617  0.079887
2       1  209  618  0.211723
3       2   68  446  0.334087

## Información adicional de la geometría del detector

<img src=https://asalzbur.web.cern.ch/asalzbur/work/tml/localToGlobal.png>


El detector está construido con losas de silicona (o módulos, rectangulares o trapezoidales), dispuestos en cilindros y discos, lo que mide la posición (o los hits) de las partículas que los atraviesan. 

Los módulos detectores están organizados en grupos detectores o identificadores de volumen por `volume_id`. Dentro de un volumen, se agrupan en capas identificadas por un `layer_id`. Cada capa puede contener arbitrariamente un número de módulos detectores, la forma geométrica más pequeña y distinta, que puede ser identificada con un `module_id`. Dentro de cada grupo, los módulos detectores son del mismo tipo, por ejemplo, tienen la misma granularidad. 

Todos los módulos detectores simulados también son llamados sensores semiconductores que son construidos de chips sensores de silicona. Cada módulo puede ser representado por una superficie sensible bidimensional, plana, acotada. Estas superficies sensibles están subdivididas en grillas regulares que definen las células detectoras, la granularidad más pequeña dentro del detector. 

# Gráficos

In [7]:
import plotly.express as px
import plotly.graph_objects as go

In [8]:
hit_position = ["hit_id", "x", "y", "z"]
layer = ["layer_id", "x", "y", "z"]
axis_columns = ["x", "y", "z"]
particle = ["particle_id", "vx", "vy", "vz", "nhits"]
animation_particle = ["particle_id", "px", "py", "pz", "nhits"]

df_axis = hits_data[axis_columns].head(10000)
df_hit = hits_data[hit_position].head(10000) 
df_layer = hits_data[layer].head(10000)
df_particle =particles_data[particle].head(10000)
df_animation_particle = particles_data[animation_particle].sort_values('nhits')

In [9]:
fig = go.Figure(data=[go.Scatter3d( x=df_layer['x'],
                        y=df_layer['y'],
                        z=df_layer['z'],
                        mode='markers',
                        marker={
                                "size":2,
                                "color":df_layer['layer_id'],
                                "colorscale": 'Viridis'
                                }
                            )
                    ]
               )

fig.show()

Se colorearon los puntos de acuerdo con la capa en la que se encuentran. Como las medidas se encuentran en milimetros, se está considerando 1.5 metros del colisionador. 

In [10]:
fig = go.Figure(data=[go.Scatter3d( x=df_particle['vx'],
                        y=df_particle['vy'],
                        z=df_particle['vz'],
                        mode='markers',
                        marker={
                                "size":5,
                                "color":df_particle['nhits'],
                                
                                }
                            )
                    ]
               )

fig.show()

Se tienen las partículas de acuerdo con la cantidad de hits de cada una de ellas. 

## Gráfico de líneas

In [11]:
df = truth_data
df = df.head(5000)

In [12]:
fig = px.line_3d(df, x='tx', y='ty', z='tz', color='particle_id')
fig.show()

## Gráfico animado

Se analiza el comportamiento de las partículas a partir de su momento inicial a lo largo del eje global (el que se encuentra representado por la variación en los colores)

In [13]:
fig = px.scatter(df_animation_particle, x='px', y='py', color='pz', animation_frame='nhits',
           hover_name='particle_id')

fig.show()

# Encontrando el valor óptimo de EPS

## ¿Qué es el DBSCAN?

DBSCAN (Density-Based Spatial Clustering and Application with Noise), es un algoritmo de clustering basado en la densidad, introducido por Ester, que puede ser utilizado para identificar clusters de cualquier forma en un dataset que contiene ruido y outliers. 

Existen dos parámetros que son importantes para DBSCAN: 
* epsilon (eps): define el radio de la vecindad en las cercanías de un punto `x`. Es llamada la ϵ-vecindad de x. 
* minimum points (MinPts): El mínimo número de vecinos dentro del radio de "eps". 

DBSCAN usa eps=0.008.



### Calculando el valor óptimo de EPS

In [14]:
from sklearn.neighbors import NearestNeighbors

In [15]:
elements = ["x", "y", "z"]
df_dbscan = hits_data[elements]

In [16]:
nbrs = NearestNeighbors(n_neighbors=5).fit(df_dbscan)
distances, indices = nbrs.kneighbors(df_dbscan)